<a href="https://colab.research.google.com/github/ChyYasir/BioSignal_Detection/blob/main/auto_encoder.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# Configure Git (only once per session)
!git config --global user.email "chyyasir2000@gmail.com"
!git config --global user.name "ChyYasir"


In [ ]:
!git clone https://github.com/ChyYasir/BioSignal_Detection.git


In [ ]:
import pandas as pd
import numpy as np
from tensorflow.keras.layers import Input, Dense, Softmax
from tensorflow.keras.models import Model
from tensorflow.keras.regularizers import l1
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.metrics import roc_curve, auc, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import interpolate
import tensorflow.keras.backend as K


In [ ]:
# @title
import pandas as pd

cesarean_df = pd.read_csv('/content/drive/MyDrive/ML/early_cesarean_features.csv')
induced_cesarean_df = pd.read_csv('/content/drive/MyDrive/ML/early_induced-cesarean_features.csv')
spontaneous_df = pd.read_csv('/content/drive/MyDrive/ML/early_spontaneous_features.csv')

cesarean_df['label'] = 0
induced_cesarean_df['label'] = 1
spontaneous_df['label'] = 2

merged_df = pd.concat([cesarean_df, induced_cesarean_df, spontaneous_df])

merged_df.to_csv('/content/drive/MyDrive/ML/features.csv', index=False)

In [ ]:
data = pd.read_csv("/content/drive/MyDrive/ML/features.csv")

X = data.drop("label", axis=1).values
y = data["label"].values

In [ ]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

num_classes = len(np.unique(y))
y_categorical = to_categorical(y, num_classes=num_classes)

# print(X_scaled)
# print(y_categorical)

In [ ]:
# Plot confusion matrix
def plot_confusion_matrix(y_true_all, y_pred_all, classes, save_path='confusion_matrix.png'):
    y_true_flat = np.concatenate([np.argmax(y_true, axis=1) for y_true in y_true_all])
    y_pred_flat = np.concatenate([np.argmax(y_pred, axis=1) for y_pred in y_pred_all])

    cm = confusion_matrix(y_true_flat, y_pred_flat)
    plt.figure(figsize=(8, 6))
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', xticklabels=classes, yticklabels=classes)
    plt.xlabel('Predicted')
    plt.ylabel('True')
    plt.title('Confusion Matrix')
    plt.savefig(save_path)
    plt.show()
    plt.close()

In [ ]:
# Plot ROC curve (multi-class, one-vs-rest)
def plot_roc_curve(y_true_all, y_score_all, num_classes, class_names, save_path='roc_curve.png'):
    mean_fpr = np.linspace(0, 1, 100)
    plt.figure(figsize=(8, 6))

    mean_tprs = []
    aucs = []

    for c in range(num_classes):
        tprs = []
        class_aucs = []
        for i in range(len(y_true_all)):
            fpr, tpr, _ = roc_curve(y_true_all[i][:, c], y_score_all[i][:, c])
            class_aucs.append(auc(fpr, tpr))
            tpr_interp = np.interp(mean_fpr, fpr, tpr)
            tpr_interp[0] = 0.0
            tprs.append(tpr_interp)

        mean_tpr = np.mean(tprs, axis=0)
        mean_tpr[-1] = 1.0
        mean_auc = auc(mean_fpr, mean_tpr)
        std_auc = np.std(class_aucs)
        aucs.append(mean_auc)

        std_tpr = np.std(tprs, axis=0)
        tprs_upper = np.minimum(mean_tpr + std_tpr, 1)
        tprs_lower = np.maximum(mean_tpr - std_tpr, 0)

        plt.plot(mean_fpr, mean_tpr, lw=2, alpha=0.8,
                 label=f'{class_names[c]} (AUC = {mean_auc:.2f} ± {std_auc:.2f})')
        plt.fill_between(mean_fpr, tprs_lower, tprs_upper, alpha=0.2)

    plt.plot([0, 1], [0, 1], 'k--', lw=2)
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title('ROC Curves (One-vs-Rest)')
    plt.legend(loc='lower right')
    plt.savefig(save_path)
    plt.show()
    plt.close()
    return np.mean(aucs)

# **One Layer**

In [ ]:
def build_ssae_model(input_dim, num_classes):
    # First and only autoencoder
    input_layer = Input(shape=(input_dim,))
    encoded = Dense(64, activation='relu', activity_regularizer=l1(10e-5))(input_layer)
    decoded = Dense(input_dim, activation='sigmoid')(encoded)

    autoencoder = Model(input_layer, decoded)
    encoder = Model(input_layer, encoded)

    print(autoencoder.summary())
    print(encoder.summary())

    # Final DNN model with softmax layer for classification
    encoded_layer = encoder(input_layer)
    output_layer = Dense(num_classes, activation='softmax')(encoded_layer)

    final_model = Model(input_layer, output_layer)

    return final_model, autoencoder, encoder

# Function to train the SSAE model with one autoencoder
def train_ssae_model(X_train, autoencoder):
    # Train the first and only autoencoder with matching input and output dimensions
    autoencoder.compile(optimizer='adam', loss='mse')
    autoencoder.fit(X_train, X_train, epochs=50, batch_size=32, shuffle=True, verbose=0)

# Function to evaluate the model
def evaluate_model(X, y, num_folds=10, num_repeats=30):
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []

    y_true_all = []
    y_score_all = []

    kf = KFold(n_splits=num_folds, shuffle=True, random_state=42)

    for repeat in range(num_repeats):
        for train_index, test_index in kf.split(X):
            X_train, X_test = X[train_index], X[test_index]
            y_train, y_test = y[train_index], y[test_index]

            final_model, autoencoder, encoder = build_ssae_model(X_train.shape[1], num_classes)

            # train_ssae_model(X_train, encoder)
            train_ssae_model(X_train, autoencoder)

            final_model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
            final_model.fit(X_train, y_train, epochs=50, batch_size=32, shuffle=True, verbose=0)

            y_pred = final_model.predict(X_test)
            y_pred_classes = np.argmax(y_pred, axis=1)
            y_true = np.argmax(y_test, axis=1)

            accuracy_list.append(accuracy_score(y_true, y_pred_classes))
            precision_list.append(precision_score(y_true, y_pred_classes, average='weighted'))
            recall_list.append(recall_score(y_true, y_pred_classes, average='weighted'))
            f1_list.append(f1_score(y_true, y_pred_classes, average='weighted'))
            y_true_all.append(y_test)
            y_score_all.append(y_pred)

    accuracy = np.mean(accuracy_list)
    precision = np.mean(precision_list)
    recall = np.mean(recall_list)
    f1 = np.mean(f1_list)

    # Plot visualizations
    class_names = ['Cesarean', 'Induced-C', 'Spontaneous']
    mean_auc = plot_roc_curve(y_true_all, y_score_all, num_classes, class_names, save_path='roc_curve.png')
    plot_confusion_matrix(y_true_all, y_score_all, classes=class_names, save_path='confusion_matrix.png')

    return accuracy, precision, recall, f1

# Evaluate the model using 10-fold cross-validation with 30 repetitions
accuracy, precision, recall, f1 = evaluate_model(X_scaled, y_categorical)

print(f"Accuracy: {accuracy:.4f}")
print(f"Precision: {precision:.4f}")
print(f"Recall: {recall:.4f}")
print(f"F1-score: {f1:.4f}")

Model: "model_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 16)]              0         
                                                                 
 dense_3 (Dense)             (None, 64)                1088      
                                                                 
 dense_4 (Dense)             (None, 16)                1040      
                                                                 
Total params: 2128 (8.31 KB)
Trainable params: 2128 (8.31 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
None
Model: "model_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 16)]              0         
                                                                 
 dens

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "model_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_3 (InputLayer)        [(None, 16)]              0         
                                                                 
 dense_6 (Dense)             (None, 64)                1088      
                                                                 
 dense_7 (Dense)             (None, 16)                1040      
                                                                 
Total params: 2128 (8.31 KB)
Trainable params: 2128 (8.31 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
None
Model: "model_8"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_3 (InputLayer)        [(None, 16)]              0         
                                                                 
 dens

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


1/1 [==============================] - 0s 60ms/step
Model: "model_13"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_5 (InputLayer)        [(None, 16)]              0         
                                                                 
 dense_12 (Dense)            (None, 64)                1088      
                                                                 
 dense_13 (Dense)            (None, 16)                1040      
                                                                 
Total params: 2128 (8.31 KB)
Trainable params: 2128 (8.31 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
None
Model: "model_14"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_5 (InputLayer)        [(None, 16)]              0         
                 

...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


1/1 [==============================] - 0s 63ms/step
Model: "model_901"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_301 (InputLayer)      [(None, 16)]              0         
                                                                 
 dense_900 (Dense)           (None, 64)                1088      
                                                                 
 dense_901 (Dense)           (None, 16)                1040      
                                                                 
Total params: 2128 (8.31 KB)
Trainable params: 2128 (8.31 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
None
Model: "model_902"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_301 (InputLayer)      [(None, 16)]              0         
               

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


1/1 [==============================] - 0s 62ms/step
Accuracy: 0.8522
Precision: 0.7424
Recall: 0.8522
F1-score: 0.7916


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


# **Two Layer**

In [ ]:


# Function to build SSAE model with two encoders
def build_ssae_model(input_dim, num_classes):
    # First autoencoder
    input_layer = Input(shape=(input_dim,))
    # encoded1 = Dense(64, activation='relu', activity_regularizer=l1(10e-5))(input_layer)
    # decoded1 = Dense(input_dim, activation='sigmoid')(encoded1)
    # encoded1 = Dense(18, activation='relu', name='encoded1', kernel_regularizer='l2')(input_layer)
    # decoded1 = Dense(input_dim, activation='sigmoid')(encoded1)
    encoded1 = Dense(18, activation='relu', name='encoded1', activity_regularizer=l1(1e-4))(input_layer)
    decoded1 = Dense(input_dim, activation='sigmoid')(encoded1)

    autoencoder1 = Model(input_layer, decoded1)
    encoder1 = Model(input_layer, encoded1)

    print(autoencoder1.summary())
    print(encoder1.summary())

    # Second autoencoder
    # input_encoded1 = Input(shape=(64,))
    # encoded2 = Dense(32, activation='relu', activity_regularizer=l1(10e-5))(input_encoded1)
    # decoded2 = Dense(64, activation='sigmoid')(encoded2)

    # input_encoded1 = Input(shape=(18,))
    # encoded2 = Dense(12, activation='relu', name='encoded2', kernel_regularizer='l2')(input_encoded1)
    # decoded2 = Dense(18, activation='sigmoid')(encoded2)

    input_encoded1 = Input(shape=(18,))
    encoded2 = Dense(12, activation='relu', name='encoded2', activity_regularizer=l1(1e-4))(input_encoded1)
    decoded2 = Dense(18, activation='sigmoid')(encoded2)

    autoencoder2 = Model(input_encoded1, decoded2)
    encoder2 = Model(input_encoded1, encoded2)

    print(autoencoder2.summary())
    print(encoder2.summary())

    # Final DNN model with softmax layer for classification
    encoded_layer1 = encoder1(input_layer)
    encoded_layer2 = encoder2(encoded_layer1)
    output_layer = Dense(num_classes, activation='softmax')(encoded_layer2)

    final_model = Model(input_layer, output_layer)

    return final_model, autoencoder1, encoder1, autoencoder2, encoder2

# Function to train SSAE model with two encoders
def train_ssae_model(X_train, autoencoder1, encoder1, autoencoder2):
    # Train the first autoencoder
    autoencoder1.compile(optimizer='adam', loss='mse')
    autoencoder1.fit(X_train, X_train, epochs=50, batch_size=32, shuffle=True, verbose=0)

    # Encode the input data using the first encoder
    X_encoded1 = encoder1.predict(X_train)

    # Train the second autoencoder using the encoded data from the first encoder
    autoencoder2.compile(optimizer='adam', loss='mse')
    autoencoder2.fit(X_encoded1, X_encoded1, epochs=50, batch_size=32, shuffle=True, verbose=0)

# Function to evaluate the SSAE model with two encoders
def evaluate_model(X, y, num_folds=10, num_repeats=30):
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []
    y_true_all = []
    y_score_all = []

    kf = KFold(n_splits=num_folds, shuffle=True, random_state=42)

    for repeat in range(num_repeats):
        for train_index, test_index in kf.split(X):
            X_train, X_test = X[train_index], X[test_index]
            y_train, y_test = y[train_index], y[test_index]

            final_model, autoencoder1, encoder1, autoencoder2, encoder2 = build_ssae_model(X_train.shape[1], num_classes)

            # Train the SSAE model
            train_ssae_model(X_train, autoencoder1, encoder1, autoencoder2)

            final_model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
            final_model.fit(X_train, y_train, epochs=50, batch_size=32, shuffle=True, verbose=0)

            y_pred = final_model.predict(X_test)
            y_pred_classes = np.argmax(y_pred, axis=1)
            y_true = np.argmax(y_test, axis=1)

            accuracy_list.append(accuracy_score(y_true, y_pred_classes))
            precision_list.append(precision_score(y_true, y_pred_classes, average='weighted'))
            recall_list.append(recall_score(y_true, y_pred_classes, average='weighted'))
            f1_list.append(f1_score(y_true, y_pred_classes, average='weighted'))

            y_true_all.append(y_test)
            y_score_all.append(y_pred)

    accuracy = np.mean(accuracy_list)
    precision = np.mean(precision_list)
    recall = np.mean(recall_list)

    f1 = np.mean(f1_list)
    # Plot visualizations
    class_names = ['Cesarean', 'Induced-C', 'Spontaneous']
    mean_auc = plot_roc_curve(y_true_all, y_score_all, num_classes, class_names, save_path='roc_curve.png')
    plot_confusion_matrix(y_true_all, y_score_all, classes=class_names, save_path='confusion_matrix.png')

    return accuracy, precision, recall, f1

# Assuming X_scaled and y_categorical are already defined and preprocessed
num_classes = y_categorical.shape[1]

# Evaluate the model using 10-fold cross-validation with 30 repetitions
accuracy, precision, recall, f1 = evaluate_model(X_scaled, y_categorical)

print(f"Accuracy: {accuracy:.4f}")
print(f"Precision: {precision:.4f}")
print(f"Recall: {recall:.4f}")
print(f"F1-score: {f1:.4f}")


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)        │ (None, 16)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ encoded1 (Dense)                │ (None, 18)             │           306 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 16)             │           304 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 610 (2.38 KB)

 Trainable params: 610 (2.38 KB)

 Non-trainable params: 0 (0.00 B)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_383 (InputLayer)    │ (None, 18)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ encoded2 (Dense)                │ (None, 12)             │           228 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 228 (912.00 B)

 Trainable params: 228 (912.00 B)

 Non-trainable params: 0 (0.00 B)

None
8/8 ━━━━━━━━━━━━━━━━━━━━ 9s 702ms/step
